# Import Statements

In [1]:
import re
from textblob import TextBlob
import pandas as pd
from wordcloud import WordCloud
import plotly.express as px
from collections import Counter
import matplotlib.pyplot as plt

# User Defined Methods

In [2]:
def removeMentions(x):
    return re.sub(r'(<m\d+>|<\/m\d+>)', '', x)

In [3]:
df_matcharticles = pd.read_csv('./data/matchArticles.txt', sep='\t', \
                              names=['matchNumber', 'articleNumber', 'title', 'subtitle', \
                                     'authorAndLocation', 'Date', 'articleText'])
df_matcharticles.head()

matchNumber  articleNumber  \
0            1         501674   
1            1         501691   
2            1         501718   
3            1         501739   
4            1         501837   

                                               title  \
0  Bangladesh v India, Group B, World Cup 2011, M...   
1  Bangladesh v India, Group B, World Cup 2011, M...   
2  Bangladesh v India, Group B, World Cup 2011, M...   
3  Bangladesh v India, Group B, World Cup 2011, M...   
4                                     World Cup 2011   

                               subtitle            authorAndLocation  \
0       Co-hosts spar in curtain raiser  The Preview by George Binoy   
1    Time for us to do our job - Shakib     Sidharth Monga in Mirpur   
2  Dhoni plays down the pressure factor         Sambit Bal in Mirpur   
3   Bullish Bangladesh ready for battle     Sidharth Monga in Mirpur   
4   Bangladesh v India, Group B, Mirpur           ESPNcricinfo staff   

                Date                                        articleText  
0  February 18, 2011  #p#Match Facts #p#February 19, Mirpur Start ti...  
1  February 18, 2011  #p#It seemed as though Shakib Al Hasan had a t...  
2  February 18, 2011  #p#On the morning of the final day of the Adel...  
3  February 18, 2011  Bangladesh will have to do without Mashrafe Mo...  
4  February 19, 2011      #p#Bangladesh v India, World Cup 2011, Mirpur

In [4]:
df_matcharticles.shape

(544, 7)

In [5]:
df_matcharticles.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 544 entries, 0 to 543
Data columns (total 7 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   matchNumber        544 non-null    int64 
 1   articleNumber      544 non-null    int64 
 2   title              519 non-null    object
 3   subtitle           534 non-null    object
 4   authorAndLocation  538 non-null    object
 5   Date               529 non-null    object
 6   articleText        544 non-null    object
dtypes: int64(2), object(5)
memory usage: 29.9+ KB


In [6]:
df_matcharticles.articleNumber.value_counts(sort='ascending')

502769    2
503673    2
505092    2
506585    1
502111    1
         ..
503491    1
505540    1
507084    1
507590    1
504835    1
Name: articleNumber, Length: 541, dtype: int64

In [7]:
df_matcharticles[df_matcharticles.articleNumber.isin([502769, 503673, 505092])]

matchNumber  articleNumber  \
53             6         502769   
70             8         502769   
100           10         503673   
139           14         503673   
207           20         505092   
262           26         505092   

                                                 title  \
53   Australia v New Zealand, Group A, World Cup 20...   
70   Australia v New Zealand, Group A, World Cup 20...   
100                                                NaN   
139                                                NaN   
207                                                NaN   
262                                                NaN   

                                              subtitle  \
53   Can Ponting lead Australia out of their spin w...   
70   Can Ponting lead Australia out of their spin w...   
100         'Chasing at Premadasa no longer difficult'   
139         'Chasing at Premadasa no longer difficult'   
207  'Solidity of middle order has helped me and Ku...   
262  'Solidity of middle order has helped me and Ku...   

               authorAndLocation               Date  \
53   The Preview by Sriram Veera  February 24, 2011   
70   The Preview by Sriram Veera  February 24, 2011   
100           Mahela Jayawardene      March 1, 2011   
139           Mahela Jayawardene      March 1, 2011   
207           Mahela Jayawardene     March 10, 2011   
262           Mahela Jayawardene     March 10, 2011   

                                           articleText  
53   #p#Match Facts #p#February 25, Nagpur Start ti...  
70   #p#Match Facts #p#February 25, Nagpur Start ti...  
100  On pitches favourable for batting, Lasith Mali...  
139  On pitches favourable for batting, Lasith Mali...  
207  'Chamara Silva's form is vital to Sri Lanka's ...  
262  'Chamara Silva's form is vital to Sri Lanka's ...

- we see duplicate articles for different matches which ideally is incorrect, need to investigate to understand the article details
- 502769, 503673, 505092

In [8]:
df_matcharticles['articleCleanedParas'] = df_matcharticles.articleText.apply(lambda x:\
                                                [removeMentions(i.strip()) for i in x.split("#p#") if i])

df_matcharticles['authorNouns'] = df_matcharticles.authorAndLocation.apply(lambda x:
                                            list(TextBlob(x).noun_phrases) if isinstance(x, str) \
                                                                           else x)

In [9]:
df_matcharticles.head()

matchNumber  articleNumber  \
0            1         501674   
1            1         501691   
2            1         501718   
3            1         501739   
4            1         501837   

                                               title  \
0  Bangladesh v India, Group B, World Cup 2011, M...   
1  Bangladesh v India, Group B, World Cup 2011, M...   
2  Bangladesh v India, Group B, World Cup 2011, M...   
3  Bangladesh v India, Group B, World Cup 2011, M...   
4                                     World Cup 2011   

                               subtitle            authorAndLocation  \
0       Co-hosts spar in curtain raiser  The Preview by George Binoy   
1    Time for us to do our job - Shakib     Sidharth Monga in Mirpur   
2  Dhoni plays down the pressure factor         Sambit Bal in Mirpur   
3   Bullish Bangladesh ready for battle     Sidharth Monga in Mirpur   
4   Bangladesh v India, Group B, Mirpur           ESPNcricinfo staff   

                Date                                        articleText  \
0  February 18, 2011  #p#Match Facts #p#February 19, Mirpur Start ti...   
1  February 18, 2011  #p#It seemed as though Shakib Al Hasan had a t...   
2  February 18, 2011  #p#On the morning of the final day of the Adel...   
3  February 18, 2011  Bangladesh will have to do without Mashrafe Mo...   
4  February 19, 2011      #p#Bangladesh v India, World Cup 2011, Mirpur   

                                 articleCleanedParas               authorNouns  
0  [Match Facts, February 19, Mirpur Start time 1...   [preview, george binoy]  
1  [It seemed as though Shakib Al Hasan had a tea...  [sidharth monga, mirpur]  
2  [On the morning of the final day of the Adelai...      [sambit bal, mirpur]  
3  [Bangladesh will have to do without Mashrafe M...  [sidharth monga, mirpur]  
4       [Bangladesh v India, World Cup 2011, Mirpur]            [espncricinfo]

# Player info

In [10]:
df_players = pd.read_csv('./data/playerURLCountryName.txt', sep='\t', \
                              names=['playerShort', 'url', 'country', 'playerName'],)
df_players.head()

playerShort                                                url  \
0         A Bagai  http://www.espncricinfo.com/icc_cricket_worldc...   
1         A Nehra  http://www.espncricinfo.com/icc_cricket_worldc...   
2       A Shahzad  http://www.espncricinfo.com/icc_cricket_worldc...   
3       AA Obanda  http://www.espncricinfo.com/icc_cricket_worldc...   
4  AB de Villiers  http://www.espncricinfo.com/icc_cricket_worldc...   

        country                     playerName  
0        Canada                   Ashish Bagai  
1         India                   Ashish Nehra  
2       England  Ajmal Shahzad (Ajmal Shehzad)  
3         Kenya                    Alex Obanda  
4  South Africa                 AB de Villiers

In [11]:
countries = [i for i in list(df_players.country.unique())]

In [12]:
df_players['playerShortLower'] = df_players.playerShort.apply(lambda x: x.lower())
df_players['playerNameLower'] = df_players.playerName.apply(lambda x: x.lower())

In [13]:
df_players.head()

playerShort                                                url  \
0         A Bagai  http://www.espncricinfo.com/icc_cricket_worldc...   
1         A Nehra  http://www.espncricinfo.com/icc_cricket_worldc...   
2       A Shahzad  http://www.espncricinfo.com/icc_cricket_worldc...   
3       AA Obanda  http://www.espncricinfo.com/icc_cricket_worldc...   
4  AB de Villiers  http://www.espncricinfo.com/icc_cricket_worldc...   

        country                     playerName playerShortLower  \
0        Canada                   Ashish Bagai          a bagai   
1         India                   Ashish Nehra          a nehra   
2       England  Ajmal Shahzad (Ajmal Shehzad)        a shahzad   
3         Kenya                    Alex Obanda        aa obanda   
4  South Africa                 AB de Villiers   ab de villiers   

                 playerNameLower  
0                   ashish bagai  
1                   ashish nehra  
2  ajmal shahzad (ajmal shehzad)  
3                    alex obanda  
4                 ab de villiers

In [14]:
a= list(df_players[['playerShortLower','playerNameLower']].agg('|'.join, axis=1))

In [15]:
players = [tuple(i.split('|')) for i in a]

In [16]:
df_players[df_players.playerName=='Shakib Al Hasan']

playerShort                                                url  \
164  Shakib Al Hasan  http://www.espncricinfo.com/icc_cricket_worldc...   

        country       playerName playerShortLower  playerNameLower  
164  Bangladesh  Shakib Al Hasan  shakib al hasan  shakib al hasan

In [17]:
df_players.head()

playerShort                                                url  \
0         A Bagai  http://www.espncricinfo.com/icc_cricket_worldc...   
1         A Nehra  http://www.espncricinfo.com/icc_cricket_worldc...   
2       A Shahzad  http://www.espncricinfo.com/icc_cricket_worldc...   
3       AA Obanda  http://www.espncricinfo.com/icc_cricket_worldc...   
4  AB de Villiers  http://www.espncricinfo.com/icc_cricket_worldc...   

        country                     playerName playerShortLower  \
0        Canada                   Ashish Bagai          a bagai   
1         India                   Ashish Nehra          a nehra   
2       England  Ajmal Shahzad (Ajmal Shehzad)        a shahzad   
3         Kenya                    Alex Obanda        aa obanda   
4  South Africa                 AB de Villiers   ab de villiers   

                 playerNameLower  
0                   ashish bagai  
1                   ashish nehra  
2  ajmal shahzad (ajmal shehzad)  
3                    alex obanda  
4                 ab de villiers

# Country WordCloud

In [104]:
countries

['Canada',
 'India',
 'England',
 'Kenya',
 'South Africa',
 'Pakistan',
 'Bangladesh',
 'Ireland',
 'Sri Lanka',
 'West Indies',
 'Netherlands',
 'Zimbabwe',
 'New Zealand',
 'Australia']

In [128]:
sum(1 for _ in re.finditer(r'india', a.lower()))

23

In [18]:
allArticles = list()
_=[allArticles.extend(i) for i in df_matcharticles.articleCleanedParas]

In [113]:
a=' '.join(df_matcharticles.articleCleanedParas[0])
a

'Match Facts February 19, Mirpur Start time 14:30 local time (08:30 GMT) Few players have as much responsibility with bat and ball as Shakib Al Hasan does for Bangladesh AFP Enlarge Related Links Matches: Bangladesh v India at Dhaka Series/Tournaments: ICC Cricket World Cup Teams: Bangladesh | India Big Picture Events unfolding in Port of Spain four years ago culminated in euphoria on one side of the Bengal border, and gloom on the other. With every dance down the wicket from Tamim Iqbal, little-fancied Bangladesh landed another blow in a series of blows that would eventually eliminate India, wearied by the weight of expectation and a discordant dressing room, from the first round of the World Cup. Four years later the teams meet again, but in a tournament protected from the domino effect of a shock like the one in Trinidad. The stakes this time are different as well, for it is not just India, overwhelming favourites again, who carry a tremendous weight of expectation. As Shakib Al Has

In [19]:
allArticles = ' '.join(allArticles)

In [20]:
countryCount = dict()
for c in countries:
    countryCount[c] = sum(1 for _ in re.finditer(r'%s'%re.escape(c.lower()), allArticles.lower()))

In [21]:
countryCount

{'Canada': 418,
 'India': 1916,
 'England': 1164,
 'Kenya': 447,
 'South Africa': 1019,
 'Pakistan': 999,
 'Bangladesh': 772,
 'Ireland': 678,
 'Sri Lanka': 822,
 'West Indies': 840,
 'Netherlands': 380,
 'Zimbabwe': 478,
 'New Zealand': 809,
 'Australia': 886}

In [22]:
df_matchAggArcticles = df_matcharticles[['matchNumber','articleCleanedParas']].\
        groupby(['matchNumber']).agg({'articleCleanedParas':'sum'}).reset_index()

## Individual Match Word Cloud

In [23]:
fig = plt.figure(figsize=(17,55))
fig.subplots_adjust(hspace=0.2, wspace=0.2)
for i in range(1, 50):
    ax = fig.add_subplot(50/3+1, 3, i)
    wc=WordCloud(width=600, height=400, max_words=100, 
                 colormap="plasma", background_color="white")
    wc.generate(' '.join(df_matchAggArcticles['articleCleanedParas'][i-1]))
    ax.imshow(wc, interpolation="bilinear")
    ax.axis("off")
    ax.title.set_text('Match - %s'%(df_matchAggArcticles['matchNumber'][i-1]))    

## All Articles

In [24]:
fig = plt.figure(figsize=(20, 15))
wc = WordCloud(width=600, height=400, max_words=100, 
                 colormap="plasma", background_color="white")
wc.generate(allArticles)
plt.imshow(wc, interpolation="bilinear")
plt.axis("off")
plt.show()